In [9]:
#!/usr/bin/env python
# -*- coding: utf-8 -*-

from topogram_client import TopogramAPIClient
from slugify import slugify
from csv import DictReader
import os
import json
import pymongo
#import musicbrainzngs
import arrow
from datetime import datetime
from pymongo import MongoClient
from collections import defaultdict
from dateutil import parser
from datetime import timedelta
import time
import pickle

In [10]:
import colorsys
def get_N_HexCol(N=20):

    HSV_tuples = [(x*1.0/N, 0.5, 0.5) for x in xrange(N)]
    hex_out = []
    for rgb in HSV_tuples:
        rgb = map(lambda x: int(x*255),colorsys.hsv_to_rgb(*rgb))
        hex_out.append("".join(map(lambda x: chr(x).encode('hex'),rgb)))
    return hex_out

In [11]:
def create_topogram(title, nodes, edges):

    print "Creating topogram '%s'"%title

    try :
        r = topogram.create_topogram(title)
    except ValueError:
        print '> Topogram already exists'
        r = topogram.get_topogram_by_name(title)
    print r
    #print r["data"][0]
    topogram_ID = r["data"]["_id"]
    print "topogram ID : %s"%topogram_ID

    # get and backup existing nodes and edges
    existing_nodes = topogram.get_nodes(topogram_ID)["data"]
    existing_edges = topogram.get_edges(topogram_ID)["data"]

    # clear existing graph
    if len(existing_nodes):
        topogram.delete_nodes([n["_id"] for n in existing_nodes])
        print "%s nodes deleted"%len(existing_nodes)
    if len(existing_edges):
        topogram.delete_edges([n["_id"] for n in existing_edges])
        print "%s edges deleted"%len(existing_edges)

    r = topogram.create_nodes(topogram_ID, nodes)
    print r
    print "%s nodes created."%len(r["data"])
    r = topogram.create_edges(topogram_ID, edges)
    print "%s edges created."%len(r["data"])

    print "done. Topogram has been updated. Check it at %s/topograms/%s"%(TOPOGRAM_URL, topogram_ID)



In [73]:
from geopy.exc import GeocoderTimedOut
from geopy.geocoders import GoogleV3
    

my_api_key = os.environ.get('MY_API_KEY', None)
#print my_api_key

def do_geocode(address,G_API_KEY):
    
    
    google_maps = GoogleV3(api_key=G_API_KEY,domain='maps.google.com')
    try:
        return google_maps.geocode(address,"exactly_one=True")
    except GeocoderTimedOut:
        return do_geocode(address)



In [12]:
# setup mongo
client = MongoClient()
db = client["bandstour"]
bandsintown =  db["minedArtists"]

# credentials
TOPOGRAM_URL = "http://localhost:3000"
#TOPOGRAM_URL = "https://app.topogram.io"
USER = "gregory.bahde@laposte.net"
PASSWORD = "matrix"


In [ ]:
with open('./iso_3166_2_mod.json') as json_data:
    iso_code_table=json.load(json_data)

# data



title = "M4P 2 the ST4RZ"
my_nodesdict = {}
my_nodes= []
my_edges = []
my_edgesdict = {}
missing_nodes=[]
# date parsing
DATETIME_FORMAT = '%Y-%m-%dT%H:%M:%S'
DATETIME_FORMAT_FOR_MSBNZ ='%Y-%m-%d'

#retrieve trip coords for each artist
dict_coords={}
colors_for_nodes_and_edges = get_N_HexCol()
with open('./labels_aliases_TOTAL.obj', 'rb') as handle:
    labels_aliases=pickle.load(handle)
node={}
for lab in labels_aliases:
    print "---------------"
    print "mbid: ",lab
    print "nom:",labels_aliases[lab]["label"]["name"]
    node["id"]=lab
    node["name"]= labels_aliases[lab]["label"]["name"]
    
    if  "area" in labels_aliases[lab]["label"]:
        print "localisation:"
        print labels_aliases[lab]["label"]["area"]["name"]
        if 'iso-3166-1-code-list' in labels_aliases[lab]["label"]["area"]:
            print labels_aliases[lab]["label"]["area"]['iso-3166-1-code-list']
            print "code iso: ",iso_code_table[labels_aliases[lab]["label"]["area"]['iso-3166-1-code-list'][0]]
            ##code iso:  {u'lat': 41.87194, u'division': u'country', u'lng': 12.567379999999957, u'code': u'IT', u'name': u'Italy'}
            node["lat"]=float(iso_code_table[labels_aliases[lab]["label"]["area"]['iso-3166-1-code-list'][0]]["lat"])
            node["lng"]=float(iso_code_table[labels_aliases[lab]["label"]["area"]['iso-3166-1-code-list'][0]]["lng"])
        else: 
            if 'iso-3166-2-code-list' in labels_aliases[lab]["label"]["area"]:
                print labels_aliases[lab]["label"]["area"]['iso-3166-2-code-list']
                print "!!!code iso 2: ",iso_code_table[labels_aliases[lab]["label"]["area"]['iso-3166-2-code-list'][0]]
                ##code iso:  {u'lat': 41.87194, u'division': u'country', u'lng': 12.567379999999957, u'code': u'IT', u'name': u'Italy'}
                try:
                    node["lat"]=float(iso_code_table[labels_aliases[lab]["label"]["area"]['iso-3166-2-code-list'][0]]["lat"])
                    node["lng"]=float(iso_code_table[labels_aliases[lab]["label"]["area"]['iso-3166-2-code-list'][0]]["lng"])
                except KeyError:
                    parent= iso_code_table[labels_aliases[lab]["label"]["area"]['iso-3166-2-code-list'][0]]["parent"]
                    node["lat"]=float(iso_code_table[parent]["lat"])
                    node["lng"]=float(iso_code_table[parent]["lng"])
                        
            else:
                print "#############",labels_aliases[lab]["label"]["area"]
                print "#############",labels_aliases[lab]["label"]["area"]['name']
                refe=labels_aliases[lab]["label"]["name"]+" "+labels_aliases[lab]["label"]["area"]["name"]
                
                if os.path.exists("./geocod_tmp_obj/"+refe+".obj")==True:
                    with open("./geocod_tmp_obj/"+refe+".obj", 'rb') as handle:
                        try:
                            loca = pickle.load(handle)
                            print loca
                        except: 
                         loca={"geometry":{"location":{"lat": "48.4371143", "lng" :"-37.3321004"}}}
                else:
                    try:
                        local= do_geocode(unicode(refe),my_api_key)
                        filehandler = open("./geocod_tmp_obj/"+refe+".obj","wb")
                        pickle.dump(local.raw,filehandler)
                        print local.raw
                        loca=local.raw
                    except: 
                     loca={"geometry":{"location":{"lat": "48.4371143", "lng" :"-37.3321004"}}}
                        
                        
                        
                print loca["geometry"]["location"]["lat"]
                node["lat"]=float(loca["geometry"]["location"]["lat"])
                node["lng"]=float(loca["geometry"]["location"]["lng"])
                
                
    if  "life-span" in labels_aliases[lab]["label"]:
        print "dates",labels_aliases[lab]["label"]["life-span"]
    if "label-relation-list" in labels_aliases[lab]["label"]:
        #print "relations", labels_aliases[lab]["label"]["label-relation-list"]
        for relation in labels_aliases[lab]["label"]["label-relation-list"]:
            #print "relation",relation
            locker=0

            if "direction" in relation: 
                if relation["direction"] == 'backward': print "APPARTIENT A"
                else:
                        print relation["direction"]
            else:
                print "EST PROPRIETAIRE DE: "
                locker=1
            print relation['target']
            print relation['label']['name']
            for target, data in labels_aliases.iteritems():
                #print "DATA",data
                #print "TARGET",target
                if target == relation['target'] :
                    print "TROUVE!!!!!!!!!!!! :)"
                    locker=1
                    
            if locker == 0:
                
                print "ABSENT, ON AJOUTE A LA LISTE DES MANQUANTS"
                missing_nodes.append(relation['target'])
    print node

                    
                    
                    
print missing_nodes
print "nombre de points manquants: ",len(missing_nodes)
#for nod in missing_nodes:
    
                    



#with open('missing_nodes.obj', 'wb') as handle:
#pickle.dump(missing_nodes, handle, protocol=pickle.HIGHEST_PROTOCOL)


---------------
mbid:  781c73fd-71d0-4309-b9bb-a3036ffc705c
nom: The Spew Records
localisation:
Italy
['IT']
code iso:  {u'lat': 41.87194, u'division': u'country', u'lng': 12.567379999999957, u'code': u'IT', u'name': u'Italy'}
dates {'begin': '2000'}
{'lat': 41.87194, 'lng': 12.567379999999957, 'id': '781c73fd-71d0-4309-b9bb-a3036ffc705c', 'name': 'The Spew Records'}
---------------
mbid:  7020b318-6b95-49d4-ab5f-7cb1fe9fd3ea
nom: N.V. Bovema
localisation:
Netherlands
['NL']
code iso:  {u'lat': 52.132633, u'division': u'country', u'lng': 5.2912659999999505, u'code': u'NL', u'name': u'Netherlands'}
dates {'ended': 'true', 'begin': '1946', 'end': '1971'}
EST PROPRIETAIRE DE: 
7e1a1cff-ffca-440a-9999-3bc7dd0a03fa
EMI-Bovema Holland
TROUVE!!!!!!!!!!!! :)
{'lat': 52.132633, 'lng': 5.2912659999999505, 'id': '7020b318-6b95-49d4-ab5f-7cb1fe9fd3ea', 'name': 'N.V. Bovema'}
---------------
mbid:  a7d455f1-93f6-4bb7-a9cf-e4514efd7e02
nom: Ulftone Music
localisation:
Germany
['DE']
code iso:  {u'la

dates {'begin': '1997'}
{'lat': 46.227638, 'lng': 2.213749000000007, 'id': '11f5c33b-9717-4bcb-9e99-2e7c7bbd1eee', 'name': 'Hammerbass'}
---------------
mbid:  2318e616-fceb-45a5-ba80-3a0e484f8f62
nom: Blackheart Entertainment
localisation:
United States
['US']
code iso:  {u'lat': 37.09024, u'division': u'country', u'lng': -95.71289100000001, u'code': u'US', u'name': u'United States'}
{'lat': 37.09024, 'lng': -95.71289100000001, 'id': '2318e616-fceb-45a5-ba80-3a0e484f8f62', 'name': 'Blackheart Entertainment'}
---------------
mbid:  48e7ffc4-b453-404c-aca9-0771cc0cddcc
nom: Astar Artes Recordings
{'lat': 37.09024, 'lng': -95.71289100000001, 'id': '48e7ffc4-b453-404c-aca9-0771cc0cddcc', 'name': 'Astar Artes Recordings'}
---------------
mbid:  8f27f6a8-8ced-4dac-be28-3d42cda607e3
nom: Small Town Records
localisation:
United Kingdom
['GB']
code iso:  {u'lat': 55.378051, u'division': u'country', u'lng': -3.43597299999999, u'code': u'GB', u'name': u'United Kingdom'}
{'lat': 55.378051, 'lng':

{'lat': 37.09024, 'lng': -95.71289100000001, 'id': '79d68f6c-d06f-43ca-8033-1ddaf456efe1', 'name': 'Committee to Keep Music Evil'}
---------------
mbid:  469a45e9-b01d-4604-9920-9290ac8fdee5
nom: Compass
localisation:
Germany
['DE']
code iso:  {u'lat': 51.165691, u'division': u'country', u'lng': 10.451526000000058, u'code': u'DE', u'name': u'Germany'}
{'lat': 51.165691, 'lng': 10.451526000000058, 'id': '469a45e9-b01d-4604-9920-9290ac8fdee5', 'name': 'Compass'}
---------------
mbid:  9679d3d8-6fa3-4bf8-b563-a0d188c9bc68
nom: Living Dead Society
localisation:
Spain
['ES']
code iso:  {u'lat': 40.463667, u'division': u'country', u'lng': -3.7492200000000366, u'code': u'ES', u'name': u'Spain'}
dates {'begin': '2004'}
{'lat': 40.463667, 'lng': -3.7492200000000366, 'id': '9679d3d8-6fa3-4bf8-b563-a0d188c9bc68', 'name': 'Living Dead Society'}
---------------
mbid:  ab23e833-df1c-4678-b707-0e7af730ece5
nom: Manhaton Records
localisation:
United Kingdom
['GB']
code iso:  {u'lat': 55.378051, u'divi

APPARTIENT A
6913b00e-bd08-4147-ab5a-b633e3f574f2
International Record Syndicate, Inc.
TROUVE!!!!!!!!!!!! :)
{'lat': 37.09024, 'lng': -95.71289100000001, 'id': 'ef99cbed-5280-4011-99ed-2d09adb4789a', 'name': 'I.R.S. Records, Inc.'}
---------------
mbid:  b2a23ef7-343c-4cef-ac0d-74373c58f456
nom: Jungle Fashion Records
localisation:
United Kingdom
['GB']
code iso:  {u'lat': 55.378051, u'division': u'country', u'lng': -3.43597299999999, u'code': u'GB', u'name': u'United Kingdom'}
{'lat': 55.378051, 'lng': -3.43597299999999, 'id': 'b2a23ef7-343c-4cef-ac0d-74373c58f456', 'name': 'Jungle Fashion Records'}
---------------
mbid:  c1fc0c7a-8244-4511-8f34-065c113403be
nom: Fool’s Gold Records
localisation:
United States
['US']
code iso:  {u'lat': 37.09024, u'division': u'country', u'lng': -95.71289100000001, u'code': u'US', u'name': u'United States'}
{'lat': 37.09024, 'lng': -95.71289100000001, 'id': 'c1fc0c7a-8244-4511-8f34-065c113403be', 'name': u'Fool\u2019s Gold Records'}
---------------
mb

EST PROPRIETAIRE DE: 
133888dc-1bad-4beb-867e-97d6a2d866b0
PressPlay
EST PROPRIETAIRE DE: 
1405c9a7-5474-4ca2-8189-9076135a563e
Cherry Red Films
TROUVE!!!!!!!!!!!! :)
EST PROPRIETAIRE DE: 
166190c6-7d72-481c-84ba-ec27dddb33f3
Sidewinder Sounds
EST PROPRIETAIRE DE: 
17e73c5e-c38a-4236-9b4e-db1477e397c1
Cherry Pop
TROUVE!!!!!!!!!!!! :)
EST PROPRIETAIRE DE: 
21d61dbb-1d38-4944-b2da-0b28928e7fa0
Grapefruit Records
EST PROPRIETAIRE DE: 
25ab5df8-e9e1-44b9-bd33-c1333f672721
Arrivederci Baby!
TROUVE!!!!!!!!!!!! :)
EST PROPRIETAIRE DE: 
31fec35c-d49b-4da0-91c4-9541290652bd
Wisecrack Records
EST PROPRIETAIRE DE: 
40fbcc48-d993-4f67-95f9-7186ec7c0ee4
Bella Casa
EST PROPRIETAIRE DE: 
44837b15-ecc6-4073-ac4a-8155e8975735
Lemon Recordings
TROUVE!!!!!!!!!!!! :)
EST PROPRIETAIRE DE: 
49896002-3f18-4be6-aabb-81135e53afd6
Delay 68
EST PROPRIETAIRE DE: 
4c86c37e-cc78-40d8-9ef3-6f7abfa21b29
British Steel
EST PROPRIETAIRE DE: 
4cc50f8c-7fce-4167-904c-190b7983559f
RPM
TROUVE!!!!!!!!!!!! :)
EST PROPRIETAIRE

...

{u'geometry': {u'location_type': u'APPROXIMATE', u'bounds': {u'northeast': {u'lat': 33.459725, u'lng': -104.475357}, u'southwest': {u'lat': 33.2801539, u'lng': -104.5862741}}, u'viewport': {u'northeast': {u'lat': 33.459725, u'lng': -104.475357}, u'southwest': {u'lat': 33.2801539, u'lng': -104.5862741}}, u'location': {u'lat': 33.3942655, u'lng': -104.5230242}}, u'formatted_address': u'Roswell, NM, USA', u'place_id': u'ChIJVe2sZRNl4oYRftfPdOQLG-Q', u'address_components': [{u'long_name': u'Roswell', u'types': [u'locality', u'political'], u'short_name': u'Roswell'}, {u'long_name': u'Chaves County', u'types': [u'administrative_area_level_2', u'political'], u'short_name': u'Chaves County'}, {u'long_name': u'New Mexico', u'types': [u'administrative_area_level_1', u'political'], u'short_name': u'NM'}, {u'long_name': u'United States', u'types': [u'country', u'political'], u'short_name': u'US'}], u'partial_match': True, u'types': [u'locality', u'political']}
33.3942655
dates {'begin': '1982'}
ES

{u'geometry': {u'location_type': u'APPROXIMATE', u'bounds': {u'northeast': {u'lat': 50.1261259, u'lng': 20.2174976}, u'southwest': {u'lat': 49.9674054, u'lng': 19.7922485}}, u'viewport': {u'northeast': {u'lat': 50.1261259, u'lng': 20.2174976}, u'southwest': {u'lat': 49.9674054, u'lng': 19.7922485}}, u'location': {u'lat': 50.06465009999999, u'lng': 19.9449799}}, u'formatted_address': u'Krak\xf3w, Poland', u'place_id': u'ChIJ0RhONcBEFkcRv4pHdrW2a7Q', u'address_components': [{u'long_name': u'Krak\xf3w', u'types': [u'locality', u'political'], u'short_name': u'Krak\xf3w'}, {u'long_name': u'Krak\xf3w County', u'types': [u'administrative_area_level_2', u'political'], u'short_name': u'Krak\xf3w County'}, {u'long_name': u'Lesser Poland Voivodeship', u'types': [u'administrative_area_level_1', u'political'], u'short_name': u'Lesser Poland Voivodeship'}, {u'long_name': u'Poland', u'types': [u'country', u'political'], u'short_name': u'PL'}, {u'long_name': u'30', u'types': [u'postal_code', u'postal_

48.4371143
dates {'ended': 'true', 'begin': '1991', 'end': '1999'}
{'lat': 48.4371143, 'lng': -37.3321004, 'id': '8dd0bc73-8edc-44d3-a212-2be8caf18c92', 'name': 'Tim/Kerr Records'}
---------------
mbid:  3bb46a66-83e6-4eb9-acd6-69d04959939a
nom: Universal Music Korea
localisation:
South Korea
['KR']
code iso:  {u'lat': 35.907757, u'division': u'country', u'lng': 127.76692200000002, u'code': u'KR', u'name': u'South Korea'}
dates {'ended': 'true', 'end': '2011'}
EST PROPRIETAIRE DE: 
3386fcce-941f-4af2-a08f-b3f1f281cb61
Cube Entertainment
APPARTIENT A
edaafb43-0124-4732-a2e3-f7a9936c8bd4
Universal Music Group International
TROUVE!!!!!!!!!!!! :)
{'lat': 35.907757, 'lng': 127.76692200000002, 'id': '3bb46a66-83e6-4eb9-acd6-69d04959939a', 'name': 'Universal Music Korea'}
---------------
mbid:  293f7248-7c2e-48d6-8109-1361fcdf5f57
nom: Bleu Electric
localisation:
France
['FR']
code iso:  {u'lat': 46.227638, u'division': u'country', u'lng': 2.213749000000007, u'code': u'FR', u'name': u'France'

{u'geometry': {u'location_type': u'APPROXIMATE', u'bounds': {u'northeast': {u'lat': 40.9175771, u'lng': -73.70027209999999}, u'southwest': {u'lat': 40.4773991, u'lng': -74.25908989999999}}, u'viewport': {u'northeast': {u'lat': 40.9175771, u'lng': -73.70027209999999}, u'southwest': {u'lat': 40.4773991, u'lng': -74.25908989999999}}, u'location': {u'lat': 40.7127753, u'lng': -74.0059728}}, u'formatted_address': u'New York, NY, USA', u'place_id': u'ChIJOwg_06VPwokRYv534QaPC8g', u'address_components': [{u'long_name': u'New York', u'types': [u'locality', u'political'], u'short_name': u'New York'}, {u'long_name': u'New York', u'types': [u'administrative_area_level_1', u'political'], u'short_name': u'NY'}, {u'long_name': u'United States', u'types': [u'country', u'political'], u'short_name': u'US'}], u'partial_match': True, u'types': [u'locality', u'political']}
40.7127753
dates {'begin': '1997'}
EST PROPRIETAIRE DE: 
247622b7-9b5f-4b8c-b35b-8a58502a348c
N-Coded Music
TROUVE!!!!!!!!!!!! :)
{'la

{u'geometry': {u'location': {u'lat': 40.6974946, u'lng': -73.9593344}, u'viewport': {u'northeast': {u'lat': 40.6988435802915, u'lng': -73.9579854197085}, u'southwest': {u'lat': 40.6961456197085, u'lng': -73.96068338029151}}, u'location_type': u'ROOFTOP'}, u'address_components': [{u'long_name': u'54', u'types': [u'street_number'], u'short_name': u'54'}, {u'long_name': u'Franklin Avenue', u'types': [u'route'], u'short_name': u'Franklin Ave'}, {u'long_name': u'Bedford-Stuyvesant', u'types': [u'neighborhood', u'political'], u'short_name': u'Bedford-Stuyvesant'}, {u'long_name': u'Brooklyn', u'types': [u'political', u'sublocality', u'sublocality_level_1'], u'short_name': u'Brooklyn'}, {u'long_name': u'Kings County', u'types': [u'administrative_area_level_2', u'political'], u'short_name': u'Kings County'}, {u'long_name': u'New York', u'types': [u'administrative_area_level_1', u'political'], u'short_name': u'NY'}, {u'long_name': u'United States', u'types': [u'country', u'political'], u'short_n

In [5]:
                node = {
                    "id" : idd,
                    "name" : slugify(venue["name"]),
                    "lat" : float(venue["latitude"]),
                    "lng" : float(venue["longitude"]),
                    "weight" : float(1),
                    "start" : date.get("datetime").isoformat(),
                    "end" : (date.get("datetime")+timedelta(days=1)).isoformat(),
                    "color" : tour_color,
                    "notes" : "name : "+slugify(venue["name"])+"  \nlat : "+str(float(venue["latitude"]))+"  \nlng :"+str(float(venue["longitude"]))+"  \n weight :"+str(1)+"  \nstart : "+str(date.get("datetime").isoformat())+"  \nend : "+str((date.get("datetime")+timedelta(days=1)).isoformat())+"  \ncolor :"+str(tour_color)
                    }
            else:
                
                node = {
                    "id" : idd,
                    "name" : slugify(venue["name"]),
                    "lat" : float(venue["latitude"]),
                    "lng" : float(venue["longitude"]),
                    "weight" : float(my_nodesdict[idd]["data"].get("weight"))+1 ,
                    "start" : my_nodesdict[idd]["data"].get("start"),
                    "end" : (date.get("datetime")+timedelta(days=1)).isoformat(),
                    "color" : tour_color,
                    "notes" : "name : "+slugify(venue["name"])+"  \nlat : "+str(float(venue["latitude"]))+"  \nlng :"+str(float(venue["longitude"]))+"  \n weight :"+str((float(my_nodesdict[idd]["data"].get("weight"))+1))+"  \nstart : "+str(my_nodesdict[idd]["data"].get("start"))+"  \nend : "+(date.get("datetime")+timedelta(days=1)).isoformat()+"  \ncolor :"+tour_color
                    
                    }
            if dateini == 0:
                dateini =1
            else:
                #print my_nodes[-1]["data"]["id"]
                #print dates[gig_indice-1]["distanceToNextGig"]
                print gig_indice
                edge = {
                    "source" : my_nodes[-1]["data"]["id"],
                    "target" : node["id"],
                    "color" :  tour_color,
                    "notes" : "distance : "+str(round(dates[gig_indice]["distanceToNextGig"],2))+" km  \n"+"source : "+my_nodes[-1]["data"]["id"]+"  target : "+node["id"]+"  \ndatesource : "+dates[gig_indice -1]["datetime"].isoformat()+"  \ndatetarget : "+dates[gig_indice]["datetime"].isoformat()+"  \ngroup:"+str(tour_indice),
    #               "weight" : float(e["weight"])
                    "start" : dates[gig_indice -1]["datetime"].isoformat(),
                    "end" : dates[gig_indice]["datetime"].isoformat(),
                    "group" : str(tour_indice)
                    
                }
                print edge
                my_edges.append({ "data" : edge })
            my_nodes.append({ "data" : node })   
            my_nodesdict[node["id"]]= { "data" : node }
            gig_indice+=1
    #print my_nodes
    #print "<=============================================>"
    #print my_nodesdict
    #print "<=============================================>"
    #print my_edges
        tour_indice +=1
        #print "coords",latitude,"/",longitude

Foo Fighters
#7f3f3f
1
{'end': '1995-03-03T19:00:00', 'target': 'satyricon45-122', 'start': '1995-02-19T19:00:00', 'color': '#7f3f3f', 'notes': 'distance : 1323.85 km  \nsource : boat-house47-122  target : satyricon45-122  \ndatesource : 1995-02-19T19:00:00  \ndatetarget : 1995-03-03T19:00:00  \ngroup:0', 'source': 'boat-house47-122', 'group': '0'}
2
{'end': '1995-03-10T19:00:00', 'target': 'spaceland34-118', 'start': '1995-03-03T19:00:00', 'color': '#7f3f3f', 'notes': 'distance : 2126.3 km  \nsource : satyricon45-122  target : spaceland34-118  \ndatesource : 1995-03-03T19:00:00  \ndatetarget : 1995-03-10T19:00:00  \ngroup:0', 'source': 'satyricon45-122', 'group': '0'}
#7f523f
0
{'end': '1995-04-17T19:00:00', 'target': 'bottleneck38-95', 'start': '1995-05-19T19:00:00', 'color': '#7f523f', 'notes': 'distance : 440.42 km  \nsource : spaceland34-118  target : bottleneck38-95  \ndatesource : 1995-05-19T19:00:00  \ndatetarget : 1995-04-17T19:00:00  \ngroup:1', 'source': 'spaceland34-118', '

4
{'end': '2015-07-19T19:00:00', 'target': 'fenway-park42-71', 'start': '2015-07-18T20:00:00', 'color': '#4c3f7f', 'notes': 'distance : 10608.0 km  \nsource : fenway-park42-71  target : fenway-park42-71  \ndatesource : 2015-07-18T20:00:00  \ndatetarget : 2015-07-19T19:00:00  \ngroup:74', 'source': 'fenway-park42-71', 'group': '74'}
5
{'end': '2015-07-24T10:00:00', 'target': 'naeba-ski-resort37139', 'start': '2015-07-19T19:00:00', 'color': '#4c3f7f', 'notes': 'distance : 7725.03 km  \nsource : fenway-park42-71  target : naeba-ski-resort37139  \ndatesource : 2015-07-19T19:00:00  \ndatetarget : 2015-07-24T10:00:00  \ngroup:74', 'source': 'fenway-park42-71', 'group': '74'}
#5f3f7f
0
{'end': '2015-08-12T19:00:00', 'target': 'rexall-place53-113', 'start': '2015-08-29T17:30:00', 'color': '#5f3f7f', 'notes': 'distance : 284.78 km  \nsource : naeba-ski-resort37139  target : rexall-place53-113  \ndatesource : 2015-08-29T17:30:00  \ndatetarget : 2015-08-12T19:00:00  \ngroup:75', 'source': 'naeba-

In [6]:
print len(my_nodesdict)

599


In [22]:
print my_nodesdict

{'concert-hall30-103': {'data': {'start': '1996-04-03T19:00:00', 'end': '1996-04-04T19:00:00', 'name': 'concert-hall', 'weight': 1.0, 'lat': 30.34, 'lng': -103.7502778, 'notes': 'name : concert-hall  \nlat : 30.34  \nlng :-103.7502778  \n weight :1  \nstart : 1996-04-03T19:00:00  \nend : 1996-04-04T19:00:00  \ncolor :#727f3f', 'id': 'concert-hall30-103', 'color': '#727f3f'}}, 'santa-barbara-bowl34-119': {'data': {'start': '1996-05-03T19:00:00', 'end': '2006-09-03T19:00:00', 'name': 'santa-barbara-bowl', 'weight': 2.0, 'lat': 34.432517, 'lng': -119.69369, 'notes': 'name : santa-barbara-bowl  \nlat : 34.432517  \nlng :-119.69369  \n weight :2.0  \nstart : 1996-05-03T19:00:00  \nend : 2006-09-03T19:00:00  \ncolor :#7f3f79', 'id': 'santa-barbara-bowl34-119', 'color': '#7f3f79'}}, 'koengen605': {'data': {'start': '2008-06-11T19:00:00', 'end': '2008-06-12T19:00:00', 'name': 'koengen', 'weight': 1.0, 'lat': 60.4009895, 'lng': 5.3176599, 'notes': 'name : koengen  \nlat : 60.4009895  \nlng :5.3

In [23]:
# connect to the topogram instance (pass debug=True params for more info )
topogram = TopogramAPIClient(TOPOGRAM_URL) #, debug=True)

# create a new user
try :
    topogram.create_user(USER, PASSWORD)
except ValueError:
    print "> User has already been created."

# login a new user if needed
resp_user_login = topogram.user_login(USER, PASSWORD)
print resp_user_login

assert(resp_user_login["status"] == "success")
assert(resp_user_login["status_code"] == 200)
my_nodesdictList = []
for key, value in my_nodesdict.iteritems():
    
    my_nodesdictList.append(value)



ERROR:topogram-client:403 Unauthorized request


> User has already been created.
{u'status': u'success', 'status_code': 200, u'data': {u'authToken': u'iJh0dqmM3urFMtm3IEDW_BMSPVax37cx3HABaVmIcc8', u'userId': u'MSreQEjksjoK2igp5'}}


In [24]:
print my_nodesdictList

[{'data': {'start': '1996-04-03T19:00:00', 'end': '1996-04-04T19:00:00', 'name': 'concert-hall', 'weight': 1.0, 'lat': 30.34, 'lng': -103.7502778, 'notes': 'name : concert-hall  \nlat : 30.34  \nlng :-103.7502778  \n weight :1  \nstart : 1996-04-03T19:00:00  \nend : 1996-04-04T19:00:00  \ncolor :#727f3f', 'id': 'concert-hall30-103', 'color': '#727f3f'}}, {'data': {'start': '1996-05-03T19:00:00', 'end': '2006-09-03T19:00:00', 'name': 'santa-barbara-bowl', 'weight': 2.0, 'lat': 34.432517, 'lng': -119.69369, 'notes': 'name : santa-barbara-bowl  \nlat : 34.432517  \nlng :-119.69369  \n weight :2.0  \nstart : 1996-05-03T19:00:00  \nend : 2006-09-03T19:00:00  \ncolor :#7f3f79', 'id': 'santa-barbara-bowl34-119', 'color': '#7f3f79'}}, {'data': {'start': '2008-06-11T19:00:00', 'end': '2008-06-12T19:00:00', 'name': 'koengen', 'weight': 1.0, 'lat': 60.4009895, 'lng': 5.3176599, 'notes': 'name : koengen  \nlat : 60.4009895  \nlng :5.3176599  \n weight :1  \nstart : 2008-06-11T19:00:00  \nend : 200

In [26]:
title = "Foo Fighters test edges and notes 4"
create_topogram(title, my_nodesdictList, my_edges)

ERROR:topogram-client:500 - Error : A topogram with the same name already exists


Creating topogram 'Foo Fighters test edges and notes 4'
> Topogram already exists
{u'status': u'success', 'status_code': 200, u'data': {u'sharedPublic': False, u'title': u'Foo Fighters test edges and notes 4', u'userId': u'MSreQEjksjoK2igp5', u'_id': u'XgTJffgaKK2YsJaFu', u'slug': u'foo-fighters-test-edges-and-notes-4', u'createdAt': u'2017-10-28T08:06:52.606Z'}, u'statusCode': 200}
topogram ID : XgTJffgaKK2YsJaFu
{u'status': u'success', 'status_code': 200, u'data': [u'Ys6e66xhFea5zE48P', u'XCh4jHdwxHDqHZzsL', u'gqsWqJ8u2A7qcezow', u'ydMwv5BkxbSFRui5w', u'CbMpzNpGjzAbYPnmP', u'qwGEM4orFtrhSjHkb', u'HY8XeDxxbHa8RXi8e', u'izdQ4kqXwYSwTaSra', u'MJsC3DQrBWr8nua3D', u'TrpF7wtMxmBRxAiCN', u'zwDCYnZ5RLMFPYyRS', u'qtdGf657Pg6BsNyGh', u'ZziSJy487f3erQKuD', u'caNCo5yf46AiniNjP', u'Rn37b9aQFCH3sQcyC', u'MD9DqwvPDXSuyosWE', u'Q7jqqPoTcFXNpEvKe', u'uHzdo6GH3WbY4HTBD', u'CegXL9tsWuY3ePfKS', u'78L8duerg8NqYuoYa', u'nSYMzWEbqiRJy5CF8', u'bT6mBETPeDrifti8K', u'KL4oEDESpqGRBA8oE', u'RFTKnPFdLFSuqM8wa', 

852 edges created.
done. Topogram has been updated. Check it at http://localhost:3000/topograms/XgTJffgaKK2YsJaFu
